### Required Libraries

In [4]:
# !pip install langchain openai pandas tiktoken pyodbc -q

In [2]:
!pip install --upgrade numexpr -q

In [1]:
!pip install featuretools==0.13.3 -q

### Importing Libraries

In [1]:
import numpy as np
import pandas as pd
import featuretools as ft
import itertools
from itertools import permutations, combinations

pd.set_option('display.max_columns', None)
pd.set_option("display.max_rows", None)

import warnings
warnings.filterwarnings('ignore')
pd.options.mode.chained_assignment = None

In [2]:
print(ft.__version__)

0.13.3


### Loading Cleaned CFI Segment Data (100 Calls)

In [3]:
data = pd.read_parquet("All_for_DPS.parquet")
data.head()

Id  channel  new_index  energy  aggression  stress  uncertainty  \
0  1082504        1          1       0           0       0            0   
1  1082504        0          1       9           0       0           15   
2  1082504        1          1       6           0       5           15   
3  1082504        1          1       7           0       5           15   
4  1082504        1          1       7           0       5           15   

   excitement  uneasy  concentration  anticipation  hesitation  energy_cross  \
0           0       0              0             0           0      0.000000   
1          15       0             24             0          16      0.000000   
2          15       0              0             0          15      0.666667   
3          22       0              0            30          12      0.000000   
4          22       0              0            30          12      0.000000   

   aggression_cross  stress_cross  uncertainty_cross  excitement_cross  \
0               0.0           0.0                0.0               0.0   
1               0.0           0.0                0.0               0.0   
2               0.0           0.0                1.0               1.0   
3               0.0           0.0                0.0               0.0   
4               0.0           0.0                0.0               0.0   

   uneasy_cross  concentration_cross  anticipation_cross  hesitation_cross  
0           0.0                  0.0                 0.0            0.0000  
1           0.0                  0.0                 0.0            0.0000  
2           0.0                  0.0                 0.0            0.9375  
3           0.0                  0.0                 0.0            0.0000  
4           0.0                  0.0                 0.0            0.0000

### Splitting Data into Agent and Customer Data

In [4]:
agent_data = data[data["channel"] == 1]
# agent_data['Unique_Index'] = range(1, len(agent_data) + 1)  # Generating unique index values
# agent_data.set_index('Unique_Index', inplace=True)
# agent_data.reset_index(inplace=True)
agent_data.head()

Id  channel  new_index  energy  aggression  stress  uncertainty  \
0  1082504        1          1       0           0       0            0   
2  1082504        1          1       6           0       5           15   
3  1082504        1          1       7           0       5           15   
4  1082504        1          1       7           0       5           15   
6  1082504        1          1       6           0       3           15   

   excitement  uneasy  concentration  anticipation  hesitation  energy_cross  \
0           0       0              0             0           0      0.000000   
2          15       0              0             0          15      0.666667   
3          22       0              0            30          12      0.000000   
4          22       0              0            30          12      0.000000   
6          15       0              9             7          16      0.666667   

   aggression_cross  stress_cross  uncertainty_cross  excitement_cross  \
0               0.0           0.0                0.0               0.0   
2               0.0           0.0                1.0               1.0   
3               0.0           0.0                0.0               0.0   
4               0.0           0.0                0.0               0.0   
6               0.0           0.0                1.0               1.0   

   uneasy_cross  concentration_cross  anticipation_cross  hesitation_cross  
0           0.0                0.000                 0.0            0.0000  
2           0.0                0.000                 0.0            0.9375  
3           0.0                0.000                 0.0            0.0000  
4           0.0                0.000                 0.0            0.0000  
6           0.0                0.375                 0.0            1.0000

In [5]:
cust_data = data[data["channel"] == 0]
# cust_data['Unique_Index'] = range(1, len(cust_data) + 1)  # Generating unique index values
# cust_data.set_index('Unique_Index', inplace=True)
# cust_data.reset_index(inplace=True)
cust_data.head()

Id  channel  new_index  energy  aggression  stress  uncertainty  \
1   1082504        0          1       9           0       0           15   
5   1082504        0          1       9           0       0           15   
10  1082504        0          1       9           0       0           15   
11  1082504        0          1       9           0       0           10   
14  1082504        0          1       9           0       0           10   

    excitement  uneasy  concentration  anticipation  hesitation  energy_cross  \
1           15       0             24             0          16      0.000000   
5           15       0             24             0          16      1.285714   
10          15       0             24             0          16      1.500000   
11          15      14              0             0          15      0.000000   
14          15      14              0             0          15      1.800000   

    aggression_cross  stress_cross  uncertainty_cross  excitement_cross  \
1                0.0           0.0           0.000000          0.000000   
5                0.0           0.0           1.000000          0.681818   
10               0.0           0.0           1.000000          0.882353   
11               0.0           0.0           0.000000          0.000000   
14               0.0           0.0           0.833333          0.882353   

    uneasy_cross  concentration_cross  anticipation_cross  hesitation_cross  
1            0.0                  0.0                 0.0          0.000000  
5            0.0                  0.0                 0.0          1.333333  
10           0.0                  0.0                 0.0          0.888889  
11           0.0                  0.0                 0.0          0.000000  
14           2.0                  0.0                 0.0          1.071429

## Mr. Corne's Code

In [6]:
def create_features(player_base_table,
                    player_base_primary_index,
                    player_base_timedate_index,
                    player_events_table,
                    player_events_primary_index,
                    player_events_timedate_index,
                    event_importantcols):
    #Add a new column which is aggregation_period units since the most recent date
    player_events_table['new_index'] = player_events_table['new_index'].astype('category')

    #Creating entity set 'es'
    es = ft.EntitySet(id = 'Entity Set')
    es = es.entity_from_dataframe(entity_id = 'player_base',
                                  dataframe = player_base_table,
                                  index = player_base_primary_index,
                                  time_index = player_base_timedate_index)
    #Add events data entity
    if 'event id' in player_events_table.columns:
        make_index = False
    else:
        make_index = True
    es = es.entity_from_dataframe(entity_id = 'player_events',
                                  dataframe = player_events_table,
                                  index = 'event id',
                                  make_index = make_index,
                                  time_index = player_events_timedate_index)
    #Set entity set relationships
    rel_id_base_to_events = ft.Relationship(es['player_base'][player_base_primary_index],
                                        es['player_events'][player_events_primary_index])
    es = es.add_relationship(rel_id_base_to_events)
    es['player_events']['new_index'].interesting_values = [1,2,3]
    seed_features = create_custom_primitives(es, event_importantcols)
    #Setting proper primitives
    agg_primitives = ['sum', 'mean', 'max', 'min', 'std']
    trans_primitives = ['month']
    where_primitives = agg_primitives
    max_depth = 2
    #Deep feature synthesis for 'es'
    feature_matrix, feature_defs = ft.dfs(entityset=es, target_entity='player_base',
                                          agg_primitives = agg_primitives,
                                          trans_primitives = trans_primitives,
                                          where_primitives = where_primitives,
                                          seed_features = seed_features,
                                          max_depth = max_depth, verbose=1)
    feature_matrix_cols_filtered = (feature_matrix.filter(regex='WHERE')).columns
    feature_matrix_cols_filtered = list(feature_matrix_cols_filtered)
    feature_matrix = feature_matrix[feature_matrix_cols_filtered]
    return feature_matrix, feature_defs

def create_custom_primitives(es, important_cols):
    seed_features = []
    #division feature
    perms = list(itertools.permutations(important_cols,2))
    for perm in perms:
        seed_features.append(np.divide(ft.Feature(np.nan_to_num(es["player_events"][perm[0]])),
                ft.Feature(np.nan_to_num(es["player_events"][perm[1]]))))
    #product feature
    combs = list(itertools.combinations(important_cols,2))
    for col in important_cols:
        combs.append((col,col))
    for comb in combs:
        seed_features.append(np.multiply(ft.Feature(np.nan_to_num(es["player_events"][comb[0]])),
                ft.Feature(np.nan_to_num(es["player_events"][comb[1]]))))
    return seed_features

agent_demodata = agent_data.groupby('Id').agg({'channel':'sum'}).reset_index()
agent_demodata.columns = ['Id','Segments']
cust_demodata = cust_data.groupby('Id').agg({'channel':'sum'}).reset_index()
cust_demodata.columns = ['Id','Segments']

agent_feats, agent_feat_defs = create_features(agent_demodata,
                                              'Id',
                                              'Segments',
                                              agent_data,
                                              'Id',
                                              'channel',
                                              ['energy', 'uneasy','hesitation','energy_cross','uncertainty_cross', 'excitement_cross', 'uneasy_cross',
                                               'hesitation_cross'])
cust_feats, cust_feat_defs = create_features(cust_demodata,
                                              'Id',
                                              'Segments',
                                              cust_data,
                                              'Id',
                                              'channel',
                                              ['energy', 'uneasy','hesitation','energy_cross','uncertainty_cross', 'excitement_cross', 'uneasy_cross',
                                               'hesitation_cross'])

Built 2221 features
Elapsed: 00:56 | Progress: 100%|██████████
Built 2221 features
Elapsed: 00:27 | Progress: 100%|██████████


### Agent Features

In [7]:
print("Total Agent Features:", len(agent_feat_defs))
print("Shape of Agent DataFrame:", agent_feats.shape)

Total Agent Features: 2221
Shape of Agent DataFrame: (6647, 1665)


In [8]:
agent_feats.head()

SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 2)  \
Id                                                                                     
2028386                                           6.754386                             
1597745                                           9.883888                             
2025990                                          25.713474                             
2028116                                           5.260854                             
2027583                                          16.834566                             

         SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 1)  \
Id                                                                                     
2028386                                           4.657826                             
1597745                                           7.827425                             
2025990                                          23.221807                             
2028116                                          12.810941                             
2027583                                          23.916680                             

         SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 3)  \
Id                                                                                     
2028386                                           1.859180                             
1597745                                           6.914208                             
2025990                                           5.373800                             
2028116                                          26.803984                             
2027583                                          31.376880                             

         SUM(player_events.uneasy * uneasy_cross WHERE new_index = 2)  \
Id                                                                      
2028386                                          24.500000              
1597745                                         784.000000              
2025990                                         374.619048              
2028116                                           0.000000              
2027583                                         205.000000              

         SUM(player_events.uneasy * uneasy_cross WHERE new_index = 1)  \
Id                                                                      
2028386                                           0.000000              
1597745                                          14.000000              
2025990                                          73.500000              
2028116                                          63.000000              
2027583                                         213.028571              

         SUM(player_events.uneasy * uneasy_cross WHERE new_index = 3)  \
Id                                                                      
2028386                                           0.000000              
1597745                                          52.500000              
2025990                                          98.285714              
2028116                                           0.000000              
2027583                                          44.333333              

         SUM(player_events.energy * hesitation_cross WHERE new_index = 2)  \
Id                                                                          
2028386                                          23.266667                  
1597745                                         201.698496                  
2025990                                         248.232733                  
2028116                                         248.684395                  
2027583                                         181.559455                  

         SUM(player_events.energy * hesitation_cross WHERE new_index = 1)  \
Id   

### Customer Features

In [9]:
print("Total Customer Features:", len(cust_feat_defs))
print("Shape of Customer DataFrame:", cust_feats.shape)

Total Customer Features: 2221
Shape of Customer DataFrame: (6647, 1665)


In [10]:
cust_feats.head()

SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 2)  \
Id                                                                                     
1082504                                          77.922896                             
1083404                                          54.000397                             
1083867                                         136.317378                             
1089026                                          64.090184                             
1090464                                          58.506373                             

         SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 1)  \
Id                                                                                     
1082504                                         155.084780                             
1083404                                          55.488249                             
1083867                                         155.633906                             
1089026                                          44.450707                             
1090464                                          41.791570                             

         SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 3)  \
Id                                                                                     
1082504                                          35.300572                             
1083404                                          28.603116                             
1083867                                          82.333283                             
1089026                                         121.560085                             
1090464                                          59.800754                             

         SUM(player_events.uneasy * uneasy_cross WHERE new_index = 2)  \
Id                                                                      
1082504                                         365.758730              
1083404                                         245.333333              
1083867                                         237.775275              
1089026                                         195.809524              
1090464                                          66.880952              

         SUM(player_events.uneasy * uneasy_cross WHERE new_index = 1)  \
Id                                                                      
1082504                                         256.748768              
1083404                                        1287.321429              
1083867                                         143.109524              
1089026                                         480.002381              
1090464                                          27.833333              

         SUM(player_events.uneasy * uneasy_cross WHERE new_index = 3)  \
Id                                                                      
1082504                                          15.083333              
1083404                                         312.392857              
1083867                                          15.502045              
1089026                                         301.833333              
1090464                                          51.761905              

         SUM(player_events.energy * hesitation_cross WHERE new_index = 2)  \
Id                                                                          
1082504                                         550.308428                  
1083404                                         732.064604                  
1083867                                         784.257682                  
1089026                                        1231.115074                  
1090464                                         922.325380                  

         SUM(player_events.energy * hesitation_cross WHERE new_index = 1)  \
Id   

### Combine Both

In [11]:
# Add prefix "agent_" to columns of agent_feats dataframe (excluding 'Id' column)
agent_feats_pre = agent_feats.copy().reset_index()
agent_feats_pre = agent_feats.rename(columns=lambda x: 'agent_' + x if x != 'Id' else x)

# Add prefix "cust_" to columns of cust_feats dataframe (excluding 'Id' column)
cust_feats_pre = cust_feats.copy().reset_index()
cust_feats_pre = cust_feats.rename(columns=lambda x: 'cust_' + x if x != 'Id' else x)

# Merge dataframes on the 'Id' column
all_df = pd.merge(agent_feats_pre, cust_feats_pre, on='Id')
print(all_df.shape)
all_df.head(2)

(6647, 3330)


agent_SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 2)  \
Id                                                                                           
2028386                                           6.754386                                   
1597745                                           9.883888                                   

         agent_SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 1)  \
Id                                                                                           
2028386                                           4.657826                                   
1597745                                           7.827425                                   

         agent_SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 3)  \
Id                                                                                           
2028386                                           1.859180                                   
1597745                                           6.914208                                   

         agent_SUM(player_events.uneasy * uneasy_cross WHERE new_index = 2)  \
Id                                                                            
2028386                                               24.5                    
1597745                                              784.0                    

         agent_SUM(player_events.uneasy * uneasy_cross WHERE new_index = 1)  \
Id                                                                            
2028386                                                0.0                    
1597745                                               14.0                    

         agent_SUM(player_events.uneasy * uneasy_cross WHERE new_index = 3)  \
Id                                                                            
2028386                                                0.0                    
1597745                                               52.5                    

         agent_SUM(player_events.energy * hesitation_cross WHERE new_index = 2)  \
Id                                                                                
2028386                                          23.266667                        
1597745                                         201.698496                        

         agent_SUM(player_events.energy * hesitation_cross WHERE new_index = 1)  \
Id                                                                                
2028386                                          43.903509                        
1597745                                         254.825765                        

         agent_SUM(player_events.energy * hesitation_cross WHERE new_index = 3)  \
Id                                                                                
2028386                                          35.852273                        
1597745                                         101.995798                        

         agent_SUM(player_events.uneasy WHERE new_index = 2)  \
Id                                                             
2028386                                                 69     
1597745                                                159     

         agent_SUM(player_events.uneasy WHERE new_index = 1)  \
Id                                                             
2028386                                                 47     
1597745                                                126     

         agent_SUM(player_events.uneasy WHERE new_index = 3)  \
Id                                                             
2028386                                                 89     
1597745                                                254     

         agent_SUM(player_events.aggression_cross WHERE new_index = 2)  \
Id                                                                       
2028386  

In [12]:
all_df.reset_index().to_parquet("All_Train_Features.parquet", index=False)

In [13]:
all_df = pd.read_parquet("All_Train_Features.parquet")
all_df.head()

Id  \
0  2028386   
1  1597745   
2  2025990   
3  2028116   
4  2027583   

   agent_SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 2)  \
0                                           6.754386                                   
1                                           9.883888                                   
2                                          25.713474                                   
3                                           5.260854                                   
4                                          16.834566                                   

   agent_SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 1)  \
0                                           4.657826                                   
1                                           7.827425                                   
2                                          23.221807                                   
3                                          12.810941                                   
4                                          23.916680                                   

   agent_SUM(player_events.uncertainty_cross / hesitation_cross WHERE new_index = 3)  \
0                                           1.859180                                   
1                                           6.914208                                   
2                                           5.373800                                   
3                                          26.803984                                   
4                                          31.376880                                   

   agent_SUM(player_events.uneasy * uneasy_cross WHERE new_index = 2)  \
0                                          24.500000                    
1                                         784.000000                    
2                                         374.619048                    
3                                           0.000000                    
4                                         205.000000                    

   agent_SUM(player_events.uneasy * uneasy_cross WHERE new_index = 1)  \
0                                           0.000000                    
1                                          14.000000                    
2                                          73.500000                    
3                                          63.000000                    
4                                         213.028571                    

   agent_SUM(player_events.uneasy * uneasy_cross WHERE new_index = 3)  \
0                                           0.000000                    
1                                          52.500000                    
2                                          98.285714                    
3                                           0.000000                    
4                                          44.333333                    

   agent_SUM(player_events.energy * hesitation_cross WHERE new_index = 2)  \
0                                          23.266667                        
1                                         201.698496                        
2                                         248.232733                        
3                                         248.684395                        
4                                         181.559455                        

   agent_SUM(player_events.energy * hesitation_cross WHERE new_index = 1)  \
0                                          43.903509                        
1                                         254.825765                        
2                                         243.661051                        
3                                         238.462866                        
4                                         138.094715                        

   agent_SUM(player_events.energy * hesitation_cross WHERE new_index = 3)  \
0               

In [14]:
all_df.shape

(6647, 3331)

In [16]:
3330/2

1665.0